<link rel="stylesheet" href="../../styles/theme_style.css">
<!--link rel="stylesheet" href="../../styles/header_style.css"-->
<link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/font-awesome/4.7.0/css/font-awesome.min.css">

<table width="100%">
    <tr>
        <td id="image_td" width="15%" class="header_image_color_4"><div id="image_img"
        class="header_image_4"></div></td>
        <td class="header_text">Fatigue Evaluation - Evolution of Median Power Frequency</td>
    </tr>
</table>

<div id="flex-container">
    <div id="diff_level" class="flex-item">
        <strong>Difficulty Level:</strong>   <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star"></span>
    </div>
    <div id="tag" class="flex-item-tag">
        <span id="tag_list">
            <table id="tag_list_table">
                <tr>
                    <td class="shield_left">Tags</td>
                    <td class="shield_right" id="tags">pre-process&#9729;emg</td>
                </tr>
            </table>
        </span>
        <!-- [OR] Visit https://img.shields.io in order to create a tag badge-->
    </div>
</div>


In contrast to the cardiac muscle, skeletal muscles are very susceptible to fatigue when exposed to an intense activity, for example, during a sports practice.

<a href="https://en.wikipedia.org/wiki/Muscle_fatigue" target="_blank">Fatigue <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a> can be defined as a complex physiological phenomenon with several causes and dependent of different mechanisms (accordingly to <a href="https://www.clinbiomech.com/article/S0268-0033(09)00025-4/fulltext" target="_blank">Cifrek et. al. <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a>).

Fatigue  may have serious consequences, being one triggering phenomenon behind muscular injuries.

So, taking into account the relevance of this phenomenon, fatigue study and monitoring is a promising research area, with some decades.
During this period, it was demonstrated that some parameters extracted from EMG signal evolve in a particular way as fatigue is being acquired.

One of these parameters, and probably the most consensual one, is the <a href="http://www.soe.uoguelph.ca/webfiles/mleuniss/Biomechanics/EMG.html" target="_blank">median power frequency<img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a>, that decreases along fatigue acquisition, i.e. the <a href="https://en.wikipedia.org/wiki/Muscle_fatigue#Electromyography" target="_blank">power spectrum suffers a compression to lowest frequency components <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a>.

In this <strong><span class="color5">Jupyter Notebook</span></strong> it will be presented the basic methodology to monitoring the fatigue along time.


<hr>

<p class="steps">1 - Importation of the needed packages</p>

In [1]:
# OpenSignals Tools own package for loading and plotting the acquired data
import biosignalsnotebooks as bsnb
import biosignalsnotebooks.signal_samples as bsnb_ss

# Scientific packages
from numpy import linspace, where
from scipy.signal import periodogram
from scipy.integrate import cumtrapz

<p class="steps">2 - Load of acquired EMG data, collected during a fatigue induction trial (<i>biceps brachii</i> isometric contraction) </p>

In [2]:
# Load of data
data, header = bsnb.load("../data/EMG_ana.h5", get_header=True)

print ("\033[1mHeader:\n\033[0m" + str(header) + "\n\033[1mData:\033[0m\n" + str(data))

Header:
{'channels': array([1]), 'comments': '', 'date': '2024-2-28', 'device': 'bitalino_rev', 'device connection': 'BTH0C:43:14:1C:2A:25', 'device name': '0C:43:14:1C:2A:25', 'digital IO': array([0, 0, 1, 1]), 'firmware version': 1282, 'resolution': array([ 4,  1,  1,  1,  1, 10]), 'sampling rate': 1000, 'sync interval': 2, 'time': '11:12:10.193', 'sensor': ['EMGBITREV'], 'column labels': {1: 'channel_1'}}
Data:
{'CH1': array([507, 509, 508, ..., 509, 507, 508], dtype=uint32)}


<p class="steps">4 - Sampling rate and acquired data samples storage (internal variables)</p>

In [3]:


ch = list(data.keys())[0]
print(f'Channel: {ch}')
sr = header["sampling rate"] # Sampling rate
print(f'Sampling rate: {sr}')
resolution = header["resolution"][-1] # Resolution
print(f'Resolution: {resolution}')

# Signal Samples
signal = data[ch]
time = linspace(0, len(signal) / sr, len(signal))


Channel: CH1
Sampling rate: 1000
Resolution: 10


<p class="steps">5 - Muscular activations detection</p>
Each muscular activation defines a processing window

In [4]:
activation_begin, activation_end = bsnb.detect_emg_activations(signal, sr)[:2]

The default call of detect_emg_activations function is:

<strong><span class="color1">detect_emg_activations(emg_signal, sample_rate, smooth_level=20, threshold_level=10, time_units=False, volts=False, resolution=None, device="biosignalsplux", plot_result=False)</span></strong>

This function returns the samples where each activation period starts and ends (first two outputs, reason why it is specified [:2]) the smoothed EMG signal samples and threshold level. 

Samples above the threshold are converted to 1 and the samples below to 0, which give rise to a rectangular activation signal.
<hr>

bsnb.detect_emg_activations previous call has explicit and implicit arguments. The list containing the signal samples collected during the acquisition and the sampling rate at which the acquisition was carried out are the explicit ones, while *smooth_level* and *threshold_level* correspond to implicit arguments that assume predefined values of 20 % and 10 %, respectively.

Changing these two parameters will produce changes in the detection of muscular activations, as can be seen at the following figure.

In [5]:
bsnb.plot_compare_act_config(signal, sr)

<p class="steps">6 - Extraction of the Median Power Frequency that characterises each muscular activation (processing window)</p>
*The Median Power Frequency is defined as the frequency value that allows the power spectrum division into two regions with equal power*

\begin{equation}
    \int_0^{f_{median}} PSD(f) df = \frac{1}{2} \int_0^{sr/2} PSD(f) df
\end{equation}
*where $f_{median}$ defines the median power frequency, $PSD(f)$ is the power spectral density estimate, after decomposing the signal by applying the Fourier Transform, for the elementary component with frequency f. The term $sr$ refers to the "sampling rate" abbreviation.*

In [6]:
# Iteration along muscular activations
median_freq_data = []
median_freq_time = []
for activation in range(0, len(activation_begin)):
    processing_window = signal[activation_begin[activation]:activation_end[activation]]
    central_point = (activation_begin[activation] + activation_end[activation]) / 2
    median_freq_time += [central_point / sr]

    # Processing window power spectrum (PSD) generation
    freqs, power = periodogram(processing_window, fs=sr)

    # Median power frequency determination
    area_freq = cumtrapz(power, freqs, initial=0)
    total_power = area_freq[-1]
    median_freq_data += [freqs[where(area_freq >= total_power / 2)[0][0]]]
    # The previous indexation [0][0] was specified in order to only the first sample that 
    # verifies the condition area_freq >= total_power / 2 be returned (all the subsequent 
    # samples will verify this condition, but, we only want the frequency that is nearest 
    # to the ideal frequency value that divides power spectrum into to regions with the 
    # same power - which is not achievable in a digital processing perspective).

<p class="steps">7 - Graphical Representation of the Median Frequency evolution time series</p>

In [7]:
bsnb.plot_median_freq_evol(time, signal, median_freq_time, median_freq_data, activation_begin, activation_end, sr)

<p class="steps">Conclusion</p>
For the present acquisition the results demonstrate that fatigue settles in during the experimental trial, meeting the behavior reported in EMG studies reviewed by <a href="https://www.clinbiomech.com/article/S0268-0033(09)00025-4/fulltext" target="_blank"><strong>Cifrek et. al. <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></strong></a> and well developed by different authors such as <a href="https://www.sciencedirect.com/science/article/pii/S1050641197000102" target="_blank"><strong>Merletti <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></strong></a> or <a href="https://www.delsys.com/Attachments_pdf/nmrc/files/2010/04/026.pdf" target="_blank"><strong>De Luca <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></strong></a>, i.e., the decrease of median power frequency.

<i>This procedure can be automatically done by <strong>fatigue_eval_med_freq</strong> function in <strong>extract</strong> module of <strong><span class="color2">biosignalsnotebooks</span></strong> package. The generated output is a pandas DataFrame</i>

<strong><span class="color7">We hope that you have enjoyed this guide. </span><span class="color2">biosignalsnotebooks</span><span class="color4"> is an environment in continuous expansion, so don't stop your journey and learn more with the remaining <a href="../MainFiles/biosignalsnotebooks.ipynb">Notebooks <img src="../../images/icons/link.png" width="10px" height="10px" style="display:inline"></a></span></strong> ! 

In [12]:

#bsnb.fatigue_eval_med_freq(signal, sr)

<span class="color6">**Auxiliary Code Segment (should not be replicated by
the user)**</span>

In [11]:
from biosignalsnotebooks.__notebook_support__ import css_style_apply
css_style_apply()

.................... CSS Style Applied to Jupyter Notebook .........................


In [12]:
%%html
<script>
    // AUTORUN ALL CELLS ON NOTEBOOK-LOAD!
    require(
        ['base/js/namespace', 'jquery'], 
        function(jupyter, $) {
            $(jupyter.events).on("kernel_ready.Kernel", function () {
                console.log("Auto-running all cells-below...");
                jupyter.actions.call('jupyter-notebook:run-all-cells-below');
                jupyter.actions.call('jupyter-notebook:save-notebook');
            });
        }
    );
</script>